In [1]:
import matplotlib as mpl
import matplotlib.pyplot as plt
import numpy as np
import sklearn
import pandas as pd
import os
import sys
import time
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.models import  Model

In [2]:
# 查看库信息
print(tf.__version__)
print(sys.version_info)
for module in mpl, np, pd, sklearn, tf, keras:
    print(module.__name__, module.__version__)

2.10.0
sys.version_info(major=3, minor=9, micro=15, releaselevel='final', serial=0)
matplotlib 3.6.2
numpy 1.23.4
pandas 1.5.1
sklearn 1.1.3
tensorflow 2.10.0
keras.api._v2.keras 2.10.0


In [3]:
# 一,处理数据
# 1,加载训练数据
# https://storage.googleapis.com/download.tensorflow.org/data/shakespeare.txt
input_filepath = "./shakespeare.txt"
text = open(input_filepath, 'r').read()
# 简单输出查看数据
# print(len(text))
# print(text[0:100])

In [4]:
# 2,生成词库
vocab = sorted(set(text))
# 查看生成的词库
# print(len(vocab))
# print(vocab)

In [5]:
# 3,生成由 字符->数字 的字典
char2idx = {char:idx for idx, char in enumerate(vocab)}
# 查看字典
# print(char2idx)

In [6]:
# 4,将词库转换为numpy中的array
idx2char = np.array(vocab)
# print(idx2char)

In [7]:
# 5,将文本转化为数字
text_as_int = np.array([char2idx[c] for c in text])
# print(text_as_int[0:10])
# print(text[0:10])

In [8]:
# 6,将数据加载到dataset中,并处理数据

# 将array转换为tensor格式的数据
char_dataset = tf.data.Dataset.from_tensor_slices(text_as_int)

# 使用tensor的方法将数据集每个100个字符进行batch分序列
seq_length = 100
seq_dataset = char_dataset.batch(seq_length + 1, drop_remainder = True)
# 选择数据查看
# for ch_id in char_dataset.take(2):
#     print(ch_id, idx2char[ch_id.numpy()])

# for seq_id in seq_dataset.take(2):
#     print(seq_id)
#     print(repr(''.join(idx2char[seq_id.numpy()])))

In [9]:
# 7,将数据分割成输入和输出两个部分
def split_input_target(id_text):
    # 将序列作如下变化 abcde -> abcd, bcde
    return id_text[0:-1], id_text[1:]
seq_dataset = seq_dataset.map(split_input_target)
# 简单查看结果
# for item_input, item_output in seq_dataset.take(2):
#     print(item_input.numpy())
#     print(item_output.numpy())

In [10]:
# 8,打乱数据,batch分组,batch_size=64
batch_size = 64
buffer_size = 10000

seq_dataset = seq_dataset.shuffle(buffer_size).batch(batch_size, drop_remainder=True)

In [11]:
# 二,构建模型
# 1,定义模型常量
vocab_size = len(vocab)
embedding_dim = 256
rnn_units = 1024

In [12]:
# 2,定义model模型
inputs = keras.Input(batch_input_shape=(batch_size,None))
print(inputs.shape)
outputs = keras.layers.Embedding(vocab_size, embedding_dim)(inputs)
print(outputs.shape)
outputs = keras.layers.LSTM(units = rnn_units,stateful = True,recurrent_initializer='glorot_uniform',return_sequences = True)(outputs)
print(outputs.shape)
outputs = keras.layers.Dense(vocab_size)(outputs)
print(outputs.shape)

model = Model(inputs, outputs)
model.summary()

(64, None)
(64, None, 256)
(64, None, 1024)
(64, None, 65)
Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(64, None)]              0         
                                                                 
 embedding (Embedding)       (64, None, 256)           16640     
                                                                 
 lstm (LSTM)                 (64, None, 1024)          5246976   
                                                                 
 dense (Dense)               (64, None, 65)            66625     
                                                                 
Total params: 5,330,241
Trainable params: 5,330,241
Non-trainable params: 0
_________________________________________________________________


In [13]:
# 3,单个例子测试模型
for input_example_batch, target_example_batch in seq_dataset.take(1):
    example_batch_predictions = model(input_example_batch)
    print(example_batch_predictions.shape)

# random sampling.
# greedy, random.
# 测试单个例子的结果
sample_indices = tf.random.categorical(logits = example_batch_predictions[0], num_samples = 1)
print(sample_indices)
# (100, 65) -> (100, 1)
sample_indices = tf.squeeze(sample_indices, axis = -1)
print(sample_indices)


# 打印输入,目标,预测的结果
print("Input: ", repr("".join(idx2char[input_example_batch[0]])))
print()
print("Output: ", repr("".join(idx2char[target_example_batch[0]])))
print()
print("Predictions: ", repr("".join(idx2char[sample_indices])))

(64, 100, 65)
tf.Tensor(
[[41]
 [46]
 [27]
 [41]
 [12]
 [26]
 [48]
 [ 0]
 [12]
 [33]
 [29]
 [50]
 [32]
 [18]
 [ 7]
 [28]
 [64]
 [25]
 [64]
 [ 8]
 [40]
 [21]
 [ 7]
 [34]
 [58]
 [37]
 [23]
 [11]
 [56]
 [ 3]
 [41]
 [42]
 [33]
 [ 9]
 [ 0]
 [41]
 [ 4]
 [62]
 [38]
 [58]
 [46]
 [64]
 [36]
 [15]
 [33]
 [14]
 [52]
 [53]
 [26]
 [12]
 [ 0]
 [28]
 [34]
 [39]
 [50]
 [51]
 [62]
 [14]
 [19]
 [16]
 [29]
 [ 7]
 [41]
 [10]
 [31]
 [52]
 [48]
 [21]
 [61]
 [23]
 [28]
 [26]
 [38]
 [ 6]
 [64]
 [62]
 [16]
 [10]
 [36]
 [27]
 [27]
 [64]
 [15]
 [64]
 [58]
 [35]
 [64]
 [ 9]
 [59]
 [25]
 [ 5]
 [11]
 [24]
 [42]
 [31]
 [50]
 [13]
 [30]
 [31]
 [51]], shape=(100, 1), dtype=int64)
tf.Tensor(
[41 46 27 41 12 26 48  0 12 33 29 50 32 18  7 28 64 25 64  8 40 21  7 34
 58 37 23 11 56  3 41 42 33  9  0 41  4 62 38 58 46 64 36 15 33 14 52 53
 26 12  0 28 34 39 50 51 62 14 19 16 29  7 41 10 31 52 48 21 61 23 28 26
 38  6 64 62 16 10 36 27 27 64 15 64 58 35 64  9 59 25  5 11 24 42 31 50
 13 30 31 51], shape=(100,), dtype=int64)

In [14]:
# 三,定义损失函数和优化器
def loss(labels, logits):
    return keras.losses.sparse_categorical_crossentropy(labels, logits, from_logits=True)

# 定义优化器和自定义损失函数
model.compile(optimizer = 'adam', loss = loss)

# 测试计算单例的损失数
example_loss = loss(target_example_batch, example_batch_predictions)
print(example_loss.shape)
print(example_loss.numpy().mean())

(64, 100)
4.1738906


In [15]:
# 四,callback模块-checkpoints
output_dir = "./text_generation_lstm3_checkpoints"
if not os.path.exists(output_dir):
    os.mkdir(output_dir)
checkpoint_prefix = os.path.join(output_dir, 'ckpt_{epoch}')
checkpoint_callback = keras.callbacks.ModelCheckpoint(filepath = checkpoint_prefix,save_weights_only = True)

In [18]:
# 五,训练模型
epochs = 100
history = model.fit(seq_dataset, epochs = epochs,callbacks = [checkpoint_callback])

# 会自动找到最近保存的变量文件
new_checkpoint = tf.train.latest_checkpoint(output_dir)

Epoch 1/100
172/172 [==============================] - 9s 47ms/step - loss: 0.4082
Epoch 2/100
172/172 [==============================] - 10s 52ms/step - loss: 0.4061
Epoch 3/100
172/172 [==============================] - 9s 46ms/step - loss: 0.4057
Epoch 4/100
172/172 [==============================] - 9s 46ms/step - loss: 0.4055
Epoch 5/100
172/172 [==============================] - 9s 45ms/step - loss: 0.4052
Epoch 6/100
172/172 [==============================] - 9s 45ms/step - loss: 0.4036
Epoch 7/100
172/172 [==============================] - 9s 47ms/step - loss: 0.4031
Epoch 8/100
172/172 [==============================] - 9s 46ms/step - loss: 0.4041
Epoch 9/100
172/172 [==============================] - 9s 48ms/step - loss: 0.4013
Epoch 10/100
172/172 [==============================] - 9s 46ms/step - loss: 0.4015
Epoch 11/100
172/172 [==============================] - 9s 46ms/step - loss: 0.4002
Epoch 12/100
172/172 [==============================] - 9s 46ms/step - loss: 0.3983


In [16]:
# 六,定义预测模型
# 1,使用checkpoint加载模型
inputs = keras.Input(batch_input_shape=(1,None))
print(inputs.shape)
outputs = keras.layers.Embedding(vocab_size, embedding_dim)(inputs)
print(outputs.shape)
outputs = keras.layers.LSTM(units = rnn_units,stateful = True,recurrent_initializer='glorot_uniform',
                        return_sequences = True)(outputs)
print(outputs.shape)
outputs = keras.layers.Dense(vocab_size)(outputs)
print(outputs.shape)

model2 = Model(inputs, outputs)
model2.load_weights(tf.train.latest_checkpoint(output_dir))
model2.summary()

(1, None)
(1, None, 256)
(1, None, 1024)
(1, None, 65)
Model: "model_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_2 (InputLayer)        [(1, None)]               0         
                                                                 
 embedding_1 (Embedding)     (1, None, 256)            16640     
                                                                 
 lstm_1 (LSTM)               (1, None, 1024)           5246976   
                                                                 
 dense_1 (Dense)             (1, None, 65)             66625     
                                                                 
Total params: 5,330,241
Trainable params: 5,330,241
Non-trainable params: 0
_________________________________________________________________


In [17]:
# 2.使用h5文件加载模型
from keras.models import load_model
model2 = load_model('model.h5', compile=False)

In [56]:
# 七,预测模型做预测
def generate_text(model, start_string, num_generate = 1000):
    input_eval = [char2idx[ch] for ch in start_string]
    input_eval = tf.expand_dims(input_eval, 0)
    
    text_generated = []
    model.reset_states()
    
    for _ in range(num_generate):
        # 输入进入模型，得到预测
        predictions = model(input_eval)
        # 去掉一维的结构
        predictions = tf.squeeze(predictions, 0)
        # 根据此位置的词库中不同字符的可能性进行采样，获得预测出的字符
        predicted_id = tf.random.categorical(predictions, num_samples = 1)[-1, 0].numpy()
        # 将预测出的字符最后一位添加到已经生成的字符串末尾
        text_generated.append(idx2char[predicted_id])
        # 将预测出的字符最后一位作为输入再次输入到模型中预测
        input_eval = tf.expand_dims([predicted_id], 0)
    return start_string + ''.join(text_generated)

new_text = generate_text(model2, "Al",8)
print(new_text)

All kiss m


In [17]:
# 将模型保存为文件，节省空间
# model2.save("model.h5")